In [1]:
import pandas as pd
import pyodbc
import numpy as np
from datetime import datetime
from dateutil.relativedelta import relativedelta
from dateutil.rrule import rrule, MONTHLY
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import cross_val_score
import plotly.express as px
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from tqdm import tqdm
from scipy.optimize import minimize
from scipy.optimize import curve_fit
from scipy.stats import halfnorm
import shap
import numdifftools as nd
from hyperopt import tpe, hp, fmin, STATUS_OK,Trials
from hyperopt.pyll.base import scope
import pickle
shap.initjs()
%load_ext autoreload
%autoreload 2
import mmm_transformations
import mmm_preprocessing
import mmm_feature_selection
import mmm_modeling
import mmm_response_curves
import mmm_optimization

# Preprocessing

In [82]:
df_pp = pd.read_csv('insmed_hcp_month_multi_channel.csv')
df_pp

InsmedID     date  rx_count  P1_Arikayce  P2_Arikayce  \
0       INSP20000000  2022-01       0.0          0.0          0.0   
1       INSP20000000  2022-02       2.0          0.0          0.0   
2       INSP20000000  2022-03       0.0          0.0          0.0   
3       INSP20000000  2022-04       0.0          0.0          0.0   
4       INSP20000000  2022-05       1.0          0.0          0.0   
...              ...      ...       ...          ...          ...   
277555  INSP20136314  2022-08       0.0          0.0          0.0   
277556  INSP20136314  2022-09       0.0          0.0          0.0   
277557  INSP20136314  2022-10       0.0          0.0          0.0   
277558  INSP20136314  2022-11       0.0          0.0          0.0   
277559  INSP20136314  2022-12       0.0          0.0          0.0   

        sfmc_opened_email  publ_pulsepoint_count  deep_intent_count Specialty  \
0                     0.0                    0.0                0.0       PUD   
1                     0.0                    0.0                0.0       PUD   
2                     0.0                    0.0                0.0       PUD   
3                     0.0                    0.0                0.0       PUD   
4                     0.0                    0.0               57.0       PUD   
...                   ...                    ...                ...       ...   
277555                0.0                   10.0                0.0       PCC   
277556                0.0                   27.0                0.0       PCC   
277557                0.0                   28.0                0.0       PCC   
277558                0.0                   38.0                0.0       PCC   
277559                0.0                   15.0                0.0       PCC   

       PrimaryState  ...  Specialty_HOS Specialty_ID  Specialty_IM  \
0                VA  ...              0            0             0   
1                VA  ...              0            0             0   
2                VA  ...              0            0             0   
3                VA  ...              0            0             0   
4                VA  ...              0            0             0   
...             ...  ...            ...          ...           ...   
277555           MO  ...              0            0             0   
277556           MO  ...              0            0             0   
277557           MO  ...              0            0             0   
277558           MO  ...              0            0             0   
277559           MO  ...              0            0             0   

        Specialty_Other  Specialty_PCC  Specialty_PDP  Specialty_PUD  \
0                     0              0              0              1   
1                     0              0              0              1   
2                     0              0              0              1   
3                     0              0              0              1   
4                     0              0              0              1   
...                 ...            ...            ...            ...   
277555                0              1              0              0   
277556                0              1              0              0   
277557                0              1              0              0   
277558                0              1              0              0   
277559                0              1              0              0   

        Segment_Current Writer  Segment_Lapsed Writer  Segment_Non-Writer  
0                            0                      1                   0  
1                            0                      1                   0  
2                            0                      1                   0  
3                            0                      1                   0  
4                            0                      1                   0  
...                        ...                  

In [83]:
cols_to_keep = ['Specialty','date','rx_count', 'P1_Arikayce', 'P2_Arikayce', 'sfmc_opened_email', 'publ_pulsepoint_count',
               'deep_intent_count']
df_pp = df_pp[cols_to_keep].groupby(['Specialty', 'date']).sum().reset_index()
df_pp = pd.concat([df_pp, pd.get_dummies(df_pp[['Specialty']])], axis=1)
df_pp

Specialty     date  rx_count  P1_Arikayce  P2_Arikayce  sfmc_opened_email  \
0          AC  2022-01       1.0          2.0          1.0               15.0   
1          AC  2022-02       1.0          5.0          0.0               12.0   
2          AC  2022-03       0.0          1.0          1.0               11.0   
3          AC  2022-04       1.0          3.0          0.0               12.0   
4          AC  2022-05       0.0          2.0          1.0               16.0   
..        ...      ...       ...          ...          ...                ...   
151       PUD  2022-08      75.0        968.0         76.0               44.0   
152       PUD  2022-09      74.0        764.0         80.0              288.0   
153       PUD  2022-10      81.0        925.0         95.0              166.0   
154       PUD  2022-11      76.0        934.0        102.0              974.0   
155       PUD  2022-12      76.0        765.0         76.0             1410.0   

     publ_pulsepoint_count  deep_intent_count  Specialty_AC  Specialty_ADU  \
0                      0.0                0.0             1              0   
1                      0.0                0.0             1              0   
2                      0.0                0.0             1              0   
3                      0.0             1947.0             1              0   
4                      0.0             1992.0             1              0   
..                     ...                ...           ...            ...   
151                51050.0           250603.0             0              0   
152                96875.0           258453.0             0              0   
153                92413.0           237472.0             0              0   
154               201356.0                0.0             0              0   
155                77298.0                0.0             0              0   

     ...  Specialty_EM  Specialty_FM  Specialty_GP  Specialty_HOS  \
0    ...             0             0             0              0   
1    ...             0             0             0              0   
2    ...             0             0             0              0   
3    ...             0             0             0              0   
4    ...             0             0             0              0   
..   ...           ...           ...           ...            ...   
151  ...             0             0             0              0   
152  ...             0             0             0              0   
153  ...             0             0             0              0   
154  ...             0             0             0              0   
155  ...             0             0             0              0   

     Specialty_ID  Specialty_IM  Specialty_Other  Specialty_PCC  \
0               0             0                0              0   
1               0             0                0              0   
2               0             0                0              0   
3               0             0                0              0   
4               0             0                0              0   
..            ...           ...              ...            ...   
151             0             0                0              0   
152             0             0                0              0   
153             0             0                0              0   
154             0             0                0              0   
155             0             0                0              0   

     Specialty_PDP  Specialty_PUD  
0                0              0  
1                0              0  
2                0              0  
3                0              0  
4                0              0  
..             ...            ...  
151              0              1  
152              0              1  
153              0              1  
154              0              1  
155              0              1  

[156 rows x 21 columns]

# Transformations

In [84]:
transform = mmm_transformations.MMMTransformations()

In [85]:
df_t = transform.lag_dv(df_pp, 'rx_count', 3, 'Specialty')
df_t = transform.lag_dv(df_t, 'P1_Arikayce', 3, 'Specialty')
df_t = transform.lag_dv(df_t, 'P2_Arikayce', 3, 'Specialty')
df_t = transform.lag_dv(df_t, 'sfmc_opened_email', 3, 'Specialty')
df_t = transform.lag_dv(df_t, 'publ_pulsepoint_count', 3, 'Specialty')
df_t = transform.lag_dv(df_t, 'deep_intent_count', 3, 'Specialty')
df_t

Specialty     date  rx_count  P1_Arikayce  P2_Arikayce  sfmc_opened_email  \
0          AC  2022-01       1.0          2.0          1.0               15.0   
1          AC  2022-02       1.0          5.0          0.0               12.0   
2          AC  2022-03       0.0          1.0          1.0               11.0   
3          AC  2022-04       1.0          3.0          0.0               12.0   
4          AC  2022-05       0.0          2.0          1.0               16.0   
..        ...      ...       ...          ...          ...                ...   
151       PUD  2022-08      75.0        968.0         76.0               44.0   
152       PUD  2022-09      74.0        764.0         80.0              288.0   
153       PUD  2022-10      81.0        925.0         95.0              166.0   
154       PUD  2022-11      76.0        934.0        102.0              974.0   
155       PUD  2022-12      76.0        765.0         76.0             1410.0   

     publ_pulsepoint_count  deep_intent_count  Specialty_AC  Specialty_ADU  \
0                      0.0                0.0             1              0   
1                      0.0                0.0             1              0   
2                      0.0                0.0             1              0   
3                      0.0             1947.0             1              0   
4                      0.0             1992.0             1              0   
..                     ...                ...           ...            ...   
151                51050.0           250603.0             0              0   
152                96875.0           258453.0             0              0   
153                92413.0           237472.0             0              0   
154               201356.0                0.0             0              0   
155                77298.0                0.0             0              0   

     ...  P2_Arikayce_lag3  sfmc_opened_email_lag1  sfmc_opened_email_lag2  \
0    ...               0.0                     0.0                     0.0   
1    ...               0.0                    15.0                     0.0   
2    ...               0.0                    12.0                    15.0   
3    ...               1.0                    11.0                    12.0   
4    ...               0.0                    12.0                    11.0   
..   ...               ...                     ...                     ...   
151  ...              55.0                   919.0                    80.0   
152  ...              81.0                    44.0                   919.0   
153  ...              84.0                   288.0                    44.0   
154  ...              76.0                   166.0                   288.0   
155  ...              80.0                   974.0                   166.0   

     sfmc_opened_email_lag3  publ_pulsepoint_count_lag1  \
0                       0.0                         0.0   
1                       0.0                         0.0   
2                       0.0                         0.0   
3                      15.0                         0.0   
4                      12.0                         0.0   
..                      ...                         ...   
151                  1049.0                     49065.0   
152                    80.0                     51050.0   
153                   919.0                     96875.0   
154                    44.0                     92413.0   
155                   288.0                    201356.0   

     publ_pulsepoint_count_lag2  publ_pulsepoint_count_lag3  \
0                           0.0                         0.0   
1                           0.0                         0.0   
2                           0.0                         0.0   
3                           0.0                         0.0   
4                           0.0                         0.0   
..                          ...                         ...   
151    

In [86]:
df_t.describe()

rx_count  P1_Arikayce  P2_Arikayce  sfmc_opened_email  \
count  156.000000   156.000000   156.000000         156.000000   
mean    22.717949   119.891026    11.769231         263.666667   
std     46.353034   231.153003    21.892065         402.783834   
min      0.000000     0.000000     0.000000           0.000000   
25%      1.000000     3.000000     0.000000          10.000000   
50%      3.000000    12.500000     1.500000          69.500000   
75%     15.000000    71.750000    10.000000         384.500000   
max    180.000000   968.000000   102.000000        1767.000000   

       publ_pulsepoint_count  deep_intent_count  Specialty_AC  Specialty_ADU  \
count             156.000000         156.000000    156.000000     156.000000   
mean            10805.282051       33769.596154      0.076923       0.076923   
std             27858.986131       74310.032367      0.267328       0.267328   
min                 0.000000           0.000000      0.000000       0.000000   
25%                 0.000000           0.000000      0.000000       0.000000   
50%               102.500000        1969.500000      0.000000       0.000000   
75%              4261.750000       16749.250000      0.000000       0.000000   
max            201356.000000      324384.000000      1.000000       1.000000   

       Specialty_CCE  Specialty_EM  ...  P2_Arikayce_lag3  \
count     156.000000    156.000000  ...        156.000000   
mean        0.076923      0.076923  ...          8.160256   
std         0.267328      0.267328  ...         18.162172   
min         0.000000      0.000000  ...          0.000000   
25%         0.000000      0.000000  ...          0.000000   
50%         0.000000      0.000000  ...          0.000000   
75%         0.000000      0.000000  ...          5.250000   
max         1.000000      1.000000  ...         84.000000   

       sfmc_opened_email_lag1  sfmc_opened_email_lag2  sfmc_opened_email_lag3  \
count              156.000000              156.000000              156.000000   
mean               222.365385              195.153846              190.724359   
std                365.905101              351.632491              353.266190   
min                  0.000000                0.000000                0.000000   
25%                  3.750000                1.000000                0.000000   
50%                 36.000000               24.500000               18.000000   
75%                196.250000              150.750000              138.500000   
max               1616.000000             1616.000000             1616.000000   

       publ_pulsepoint_count_lag1  publ_pulsepoint_count_lag2  \
count                  156.000000                  156.000000   
mean                  9282.192308                 5469.602564   
std                  26956.754958                16337.387461   
min                      0.000000                    0.000000   
25%                      0.000000                    0.000000   
50%                      0.000000                    0.000000   
75%                   2284.750000                  712.500000   
max                 201356.000000                96875.000000   

       publ_pulsepoint_count_lag3  deep_intent_count_lag1  \
count                  156.000000              156.000000   
mean                  3758.538462            33769.596154   
std                  13269.753494            74310.032367   
min                      0.000000                0.000000   
25%                      0.000000                0.000000   
50%                      0.000000             1969.500000   
75%                     69.750000            16749.250000   
max                  96875.000000           324384.000000   

       deep_intent_count_lag2  deep_intent_count_lag3  
count              156.000000              156.000000  
mean             33769.596154            29046.179487  
std              74310.032367            69785.952497  
min                  0.000000                0.000000

In [87]:
cols = ['rx_count', 'P1_Arikayce', 'P2_Arikayce', 'sfmc_opened_email', 'publ_pulsepoint_count', 'deep_intent_count']
df_t = transform.add_noise(df_t, cols, 0.25)
df_t

Specialty     date    rx_count  P1_Arikayce  P2_Arikayce  \
0          AC  2022-01    1.000000     2.000000     1.000000   
1          AC  2022-02    1.000000     5.000000     0.000000   
2          AC  2022-03    0.000000     1.000000    18.882207   
3          AC  2022-04   21.536996     3.000000     0.000000   
4          AC  2022-05    0.000000     2.000000     1.000000   
..        ...      ...         ...          ...          ...   
151       PUD  2022-08   22.860258   968.000000    22.171269   
152       PUD  2022-09   74.000000   112.610618     0.806750   
153       PUD  2022-10   81.000000   925.000000    95.000000   
154       PUD  2022-11   76.000000   934.000000   102.000000   
155       PUD  2022-12  100.214789   765.000000    76.000000   

     sfmc_opened_email  publ_pulsepoint_count  deep_intent_count  \
0            15.000000               0.000000            0.00000   
1            12.000000           75819.656781            0.00000   
2            11.000000               0.000000            0.00000   
3            12.000000               0.000000         4732.64476   
4            16.000000           15663.738361         1992.00000   
..                 ...                    ...                ...   
151          44.000000           51050.000000       250603.00000   
152         288.000000           11217.735083       258453.00000   
153         344.907515           92413.000000       237472.00000   
154         143.462459          201356.000000            0.00000   
155         104.084821           77298.000000            0.00000   

     Specialty_AC  Specialty_ADU  ...  P2_Arikayce_lag3  \
0               1              0  ...               0.0   
1               1              0  ...               0.0   
2               1              0  ...               0.0   
3               1              0  ...               1.0   
4               1              0  ...               0.0   
..            ...            ...  ...               ...   
151             0              0  ...              55.0   
152             0              0  ...              81.0   
153             0              0  ...              84.0   
154             0              0  ...              76.0   
155             0              0  ...              80.0   

     sfmc_opened_email_lag1  sfmc_opened_email_lag2  sfmc_opened_email_lag3  \
0                       0.0                     0.0                     0.0   
1                      15.0                     0.0                     0.0   
2                      12.0                    15.0                     0.0   
3                      11.0                    12.0                    15.0   
4                      12.0                    11.0                    12.0   
..                      ...                     ...                     ...   
151                   919.0                    80.0                  1049.0   
152                    44.0                   919.0                    80.0   
153                   288.0                    44.0                   919.0   
154                   166.0                   288.0                    44.0   
155                   974.0                   166.0                   288.0   

     publ_pulsepoint_count_lag1  publ_pulsepoint_count_lag2  \
0                           0.0                         0.0   
1                           0.0                         0.0   
2                           0.0                         0.0   
3                           0.0                         0.0   
4                           0.0                         0.0   
..                          ...                         ...   
151                     49065.0                         0.0   
152                     51050.0                     49065.0   
153                     96875.0                     51050.0   
154                     92413.0                     96875.0   
155                    201356.0                     92413.0   

   

In [88]:
df_t.describe()

rx_count  P1_Arikayce  P2_Arikayce  sfmc_opened_email  \
count  156.000000   156.000000   156.000000         156.000000   
mean    27.275655   130.685755    13.126646         236.604926   
std     42.888223   213.454993    20.561758         318.847822   
min      0.000000     0.000000     0.000000           0.000000   
25%      1.000000     5.000000     0.484568          17.500000   
50%      7.436563    31.353771     3.008861          95.017124   
75%     31.727700   135.571628    16.017926         359.578765   
max    178.000000   968.000000   102.000000        1767.000000   

       publ_pulsepoint_count  deep_intent_count  Specialty_AC  Specialty_ADU  \
count             156.000000         156.000000    156.000000     156.000000   
mean            13870.466605       38692.668265      0.076923       0.076923   
std             27449.872709       62992.536151      0.267328       0.267328   
min                 0.000000           0.000000      0.000000       0.000000   
25%                 0.000000           0.000000      0.000000       0.000000   
50%              1052.500000        7049.000000      0.000000       0.000000   
75%             17824.220102       60577.958642      0.000000       0.000000   
max            201356.000000      324384.000000      1.000000       1.000000   

       Specialty_CCE  Specialty_EM  ...  P2_Arikayce_lag3  \
count     156.000000    156.000000  ...        156.000000   
mean        0.076923      0.076923  ...          8.160256   
std         0.267328      0.267328  ...         18.162172   
min         0.000000      0.000000  ...          0.000000   
25%         0.000000      0.000000  ...          0.000000   
50%         0.000000      0.000000  ...          0.000000   
75%         0.000000      0.000000  ...          5.250000   
max         1.000000      1.000000  ...         84.000000   

       sfmc_opened_email_lag1  sfmc_opened_email_lag2  sfmc_opened_email_lag3  \
count              156.000000              156.000000              156.000000   
mean               222.365385              195.153846              190.724359   
std                365.905101              351.632491              353.266190   
min                  0.000000                0.000000                0.000000   
25%                  3.750000                1.000000                0.000000   
50%                 36.000000               24.500000               18.000000   
75%                196.250000              150.750000              138.500000   
max               1616.000000             1616.000000             1616.000000   

       publ_pulsepoint_count_lag1  publ_pulsepoint_count_lag2  \
count                  156.000000                  156.000000   
mean                  9282.192308                 5469.602564   
std                  26956.754958                16337.387461   
min                      0.000000                    0.000000   
25%                      0.000000                    0.000000   
50%                      0.000000                    0.000000   
75%                   2284.750000                  712.500000   
max                 201356.000000                96875.000000   

       publ_pulsepoint_count_lag3  deep_intent_count_lag1  \
count                  156.000000              156.000000   
mean                  3758.538462            33769.596154   
std                  13269.753494            74310.032367   
min                      0.000000                0.000000   
25%                      0.000000                0.000000   
50%                      0.000000             1969.500000   
75%                     69.750000            16749.250000   
max                  96875.000000           324384.000000   

       deep_intent_count_lag2  deep_intent_count_lag3  
count              156.000000              156.000000  
mean             33769.596154            29046.179487  
std              74310.032367            69785.952497  
min                  0.000000                0.000000

In [281]:
df_t[['Specialty', 'date', 'rx_count', 'P1_Arikayce', 'P2_Arikayce', 'sfmc_opened_email', 'publ_pulsepoint_count', 'deep_intent_count']].to_csv('insmed_segment_month_multi_channel_bayesian_model.csv', index=False)

In [12]:
chk = df_t[['Specialty', 'rx_count', 'P1_Arikayce', 'P2_Arikayce', 'sfmc_opened_email', 'publ_pulsepoint_count', 'deep_intent_count']]
chk.groupby('Specialty').agg({'rx_count': ['mean', 'max'], 'P1_Arikayce': ['mean', 'max'],
                             'P2_Arikayce': ['mean', 'max'], 'sfmc_opened_email': ['mean', 'max'],
                             'publ_pulsepoint_count': ['mean', 'max'], 'deep_intent_count': ['mean', 'max']}).reset_index()

Specialty    rx_count             P1_Arikayce             P2_Arikayce  \
                    mean         max        mean         max        mean   
0         AC    0.666667    2.000000    2.333333    6.000000    2.251203   
1        ADU    9.252974   82.216975    5.750000   12.000000    5.355627   
2        CCE    0.750000    2.000000    4.416667    8.000000    0.750000   
3         EM    0.096404    1.000000    0.916667    4.000000    0.000000   
4         FM    3.400641   15.807689   99.437245  606.221731    4.322811   
5         GP    3.583333   10.000000   14.710986   26.000000    1.264982   
6        HOS    5.693614   43.128588   21.930497  207.165968    0.464431   
7         ID  165.333333  180.000000  555.416667  712.000000   43.166667   
8         IM   15.916667   24.000000  109.083333  167.000000   18.619420   
9      Other   19.953208   59.438498   67.250000   90.000000    8.028226   
10       PCC    7.833333   14.000000   76.687209  313.246511    7.500000   
11       PDP    2.083333    7.000000   37.183598  317.500194    0.000000   
12       PUD   75.108381   94.000000  647.848347  934.000000   71.416667   

               sfmc_opened_email              publ_pulsepoint_count  \
           max              mean          max                  mean   
0    22.014439         18.320802   135.849623            398.416667   
1    52.267529         20.000000    43.000000            953.822970   
2     2.000000         42.806664   432.679969            482.781156   
3     0.000000        124.666667   243.000000            404.250000   
4    10.000000        329.083333   606.000000          11656.166667   
5     6.179780         85.030105   284.361257           6941.884917   
6     4.573177         76.372138   176.000000           2131.916667   
7    61.000000        465.827924   880.000000          39615.833333   
8    34.433046        521.945764  1075.000000          19395.833333   
9    21.338717        985.915498  1767.000000          17394.684325   
10   12.000000         47.000000    83.000000           9559.189798   
11    0.000000          0.416667     2.000000            347.166667   
12  102.000000        770.400116  1410.000000          45969.342190   

                  deep_intent_count                 
              max              mean            max  
0     1912.000000       1314.833333    2450.000000  
1     4694.875646       5974.490864   36341.951604  
2     2646.373875       1644.916667    3448.000000  
3     1746.000000       6459.023447   67477.281363  
4    51028.000000      34348.838148   88458.057782  
5    54117.619006       9360.666667   19419.000000  
6     8442.000000       5341.833333   12879.000000  
7   163206.000000     157453.416667  324384.000000  
8    82558.000000      49987.333333  106614.000000  
9    55378.000000      39801.887531   73713.650370  
10   56862.316376       8929.583333   17290.000000  
11    1114.000000       9893.839819   88659.286449  
12  201356.000000     119580.946660  264437.000000

# Model Fitting

In [89]:
modeling = mmm_modeling.MMMModeling()

In [90]:
# modeling
channels = ['P1_Arikayce', 'P2_Arikayce', 'sfmc_opened_email', 'publ_pulsepoint_count', 'deep_intent_count']
specialties = [x for x in df_t.columns if x.startswith('Specialty_')]
lag_dv = [x for x in df_t.columns if 'rx_count_lag' in x]
lag_channels = [x for x in df_t.columns if ('lag' in x) & ('rx_count' not in x)]
X = df_t[channels + lag_channels + lag_dv + specialties]
#X = df_t[channels + lag_channels + specialties]
y = df_t['rx_count']
model = modeling.rf_regressor(df_t, X.columns.tolist(), 'rx_count', 'date')

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_modeling.py:54: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_modeling.py:55: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [63]:
pickle.dump(model, open('rf_insmed_multichannel_w_lagchannels_lag_dv.sav', 'wb'))

In [64]:
model = pickle.load(open('rf_insmed_multichannel_w_lagchannels_lag_dv.sav', 'rb'))

In [91]:
# performance
model['performance']

{'full': {'r2': 0.9396862949931752,
  'rmse': 10.499040408925973,
  'mape': 1.646577301090463},
 'train': {'r2': 0.9334270127081541,
  'rmse': 11.223774483264716,
  'mape': 1.4531626128007014},
 'test': {'r2': 0.3559917486939145,
  'rmse': 31.034648296598593,
  'mape': 7.300817258728735}}

In [92]:
# importance
model['importance']

feature  importance       std
5             P1_Arikayce_lag1    0.358331  0.306320
20               rx_count_lag1    0.148095  0.243204
21               rx_count_lag2    0.122898  0.241710
30                Specialty_ID    0.061121  0.156008
22               rx_count_lag3    0.025539  0.067194
1                  P2_Arikayce    0.023686  0.047221
8             P2_Arikayce_lag1    0.021263  0.080440
35               Specialty_PUD    0.020788  0.042583
6             P1_Arikayce_lag2    0.020570  0.042243
7             P1_Arikayce_lag3    0.019923  0.039826
0                  P1_Arikayce    0.019295  0.029740
11      sfmc_opened_email_lag1    0.019024  0.018278
2            sfmc_opened_email    0.017256  0.018744
12      sfmc_opened_email_lag2    0.015985  0.025142
3        publ_pulsepoint_count    0.013697  0.032440
14  publ_pulsepoint_count_lag1    0.012045  0.020398
4            deep_intent_count    0.010504  0.015474
13      sfmc_opened_email_lag3    0.009333  0.012779
16  publ_pulsepoint_count_lag3    0.008846  0.019352
15  publ_pulsepoint_count_lag2    0.008125  0.013713
10            P2_Arikayce_lag3    0.006980  0.020481
17      deep_intent_count_lag1    0.005860  0.011085
18      deep_intent_count_lag2    0.005747  0.009110
28                Specialty_GP    0.005652  0.013302
19      deep_intent_count_lag3    0.005106  0.009560
9             P2_Arikayce_lag2    0.003872  0.007777
29               Specialty_HOS    0.003344  0.011763
24               Specialty_ADU    0.003135  0.006871
25               Specialty_CCE    0.001628  0.006656
27                Specialty_FM    0.000575  0.001934
33               Specialty_PCC    0.000443  0.001347
31                Specialty_IM    0.000404  0.001185
34               Specialty_PDP    0.000388  0.001294
32             Specialty_Other    0.000273  0.001515
26                Specialty_EM    0.000191  0.000727
23                Specialty_AC    0.000077  0.000427

In [93]:
# scatter plot of predictions
plot_df = pd.DataFrame({'date': model['df_preds_test']['date'].astype(str),
                        'preds': model['df_preds_test']['preds_test'],
                        'actual': model['df_preds_test']['rx_count']})
fig = px.scatter(plot_df, x="date", y=plot_df.columns.tolist(), title="Future Hold Out Set")
fig.show()

In [94]:
# scatter plot of predictions
plot_df = pd.DataFrame({'date': model['df_preds_full']['date'].astype(str),
                        'preds': model['df_preds_full']['preds_full'],
                        'actual': model['df_preds_full']['rx_count']})
fig = px.scatter(plot_df, x="date", y=plot_df.columns.tolist(), title="Random Forest - Model trained on full data")
fig.show()

# Response Curves - Isolated Impact

In [96]:
response_curves = mmm_response_curves.MMMResponseCurves()

In [97]:
channels = ['P1_Arikayce', 'P2_Arikayce', 'sfmc_opened_email', 'publ_pulsepoint_count', 'deep_intent_count']
specialties = [x for x in df_t.columns if x.startswith('Specialty_')]
lag_dv = [x for x in df_t.columns if 'rx_count_lag' in x]
lag_channels = [x for x in df_t.columns if ('lag' in x) & ('rx_count' not in x)]
X = df_t[channels + lag_channels + lag_dv + specialties + ['Specialty', 'date']]
#X = df_t[channels + lag_channels + specialties + ['Specialty', 'date']]
#X[channels + lag_channels + specialties] = 0
X[channels + lag_channels] = 0
p1_lags = [x for x in lag_channels if 'P1' in x]
p2_lags = [x for x in lag_channels if 'P2' in x]
email_lags = [x for x in lag_channels if 'email' in x]
pulse_lags = [x for x in lag_channels if 'pulse' in x]
deep_lags = [x for x in lag_channels if 'deep' in x]

D:\Users\hartsingh\AppData\Roaming\Python\Python37\site-packages\pandas\core\frame.py:3645: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [98]:
df_t.describe()

rx_count  P1_Arikayce  P2_Arikayce  sfmc_opened_email  \
count  156.000000   156.000000   156.000000         156.000000   
mean    27.275655   130.685755    13.126646         236.604926   
std     42.888223   213.454993    20.561758         318.847822   
min      0.000000     0.000000     0.000000           0.000000   
25%      1.000000     5.000000     0.484568          17.500000   
50%      7.436563    31.353771     3.008861          95.017124   
75%     31.727700   135.571628    16.017926         359.578765   
max    178.000000   968.000000   102.000000        1767.000000   

       publ_pulsepoint_count  deep_intent_count  Specialty_AC  Specialty_ADU  \
count             156.000000         156.000000    156.000000     156.000000   
mean            13870.466605       38692.668265      0.076923       0.076923   
std             27449.872709       62992.536151      0.267328       0.267328   
min                 0.000000           0.000000      0.000000       0.000000   
25%                 0.000000           0.000000      0.000000       0.000000   
50%              1052.500000        7049.000000      0.000000       0.000000   
75%             17824.220102       60577.958642      0.000000       0.000000   
max            201356.000000      324384.000000      1.000000       1.000000   

       Specialty_CCE  Specialty_EM  ...  P2_Arikayce_lag3  \
count     156.000000    156.000000  ...        156.000000   
mean        0.076923      0.076923  ...          8.160256   
std         0.267328      0.267328  ...         18.162172   
min         0.000000      0.000000  ...          0.000000   
25%         0.000000      0.000000  ...          0.000000   
50%         0.000000      0.000000  ...          0.000000   
75%         0.000000      0.000000  ...          5.250000   
max         1.000000      1.000000  ...         84.000000   

       sfmc_opened_email_lag1  sfmc_opened_email_lag2  sfmc_opened_email_lag3  \
count              156.000000              156.000000              156.000000   
mean               222.365385              195.153846              190.724359   
std                365.905101              351.632491              353.266190   
min                  0.000000                0.000000                0.000000   
25%                  3.750000                1.000000                0.000000   
50%                 36.000000               24.500000               18.000000   
75%                196.250000              150.750000              138.500000   
max               1616.000000             1616.000000             1616.000000   

       publ_pulsepoint_count_lag1  publ_pulsepoint_count_lag2  \
count                  156.000000                  156.000000   
mean                  9282.192308                 5469.602564   
std                  26956.754958                16337.387461   
min                      0.000000                    0.000000   
25%                      0.000000                    0.000000   
50%                      0.000000                    0.000000   
75%                   2284.750000                  712.500000   
max                 201356.000000                96875.000000   

       publ_pulsepoint_count_lag3  deep_intent_count_lag1  \
count                  156.000000              156.000000   
mean                  3758.538462            33769.596154   
std                  13269.753494            74310.032367   
min                      0.000000                0.000000   
25%                      0.000000                0.000000   
50%                      0.000000             1969.500000   
75%                     69.750000            16749.250000   
max                  96875.000000           324384.000000   

       deep_intent_count_lag2  deep_intent_count_lag3  
count              156.000000              156.000000  
mean             33769.596154            29046.179487  
std              74310.032367            69785.952497  
min                  0.000000                0.000000

In [99]:
# overall response curves
channel1 = response_curves.responses('overall', model['full_model'], X, 'P1_Arikayce', 1000, 5, 'Specialty', 'date', p1_lags)
channel2 = response_curves.responses('overall', model['full_model'], X, 'P2_Arikayce', 200, 1, 'Specialty', 'date', p2_lags)
channel3 = response_curves.responses('overall', model['full_model'], X, 'sfmc_opened_email', 2000, 10, 'Specialty', 'date', email_lags)
channel4 = response_curves.responses('overall', model['full_model'], X, 'publ_pulsepoint_count', 15000, 100, 'Specialty', 'date', pulse_lags)
channel5 = response_curves.responses('overall', model['full_model'], X, 'deep_intent_count', 35000, 100, 'Specialty', 'date', deep_lags)

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

...

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in power



Error - curve_fit failed


D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in true_divide

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

invalid value encountered in true_divide



In [100]:
response_curves.plot(channel1['resp_df'], 'touches', ['P1_Arikayce', 'P1_Arikayce_hill_estimate'])

In [101]:
response_curves.plot(channel2['resp_df'], 'touches', ['P2_Arikayce', 'P2_Arikayce_hill_estimate'])

In [102]:
response_curves.plot(channel3['resp_df'], 'touches', ['sfmc_opened_email', 'sfmc_opened_email_hill_estimate'])

In [103]:
response_curves.plot(channel4['resp_df'], 'touches', ['publ_pulsepoint_count', 'publ_pulsepoint_count_hill_estimate'])

In [104]:
response_curves.plot(channel5['resp_df'], 'touches', ['deep_intent_count', 'deep_intent_count_hill_estimate'])

In [105]:
channel1_segment = response_curves.responses('segment', model['full_model'], X, 'P1_Arikayce', 1000, 5, 'Specialty', 'date', p1_lags)

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in power

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in power

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero

In [106]:
channel1_segment['fig_raw']

In [107]:
channel1_segment['fig_hill']

In [108]:
channel2_segment = response_curves.responses('segment', model['full_model'], X, 'P2_Arikayce', 200, 1, 'Specialty', 'date', p2_lags)

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in power

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in power

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero

In [109]:
channel2_segment['fig_raw']

In [110]:
channel2_segment['fig_hill']

In [111]:
channel3_segment = response_curves.responses('segment', model['full_model'], X, 'sfmc_opened_email', 2000, 10, 'Specialty', 'date', email_lags)

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in power

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_

In [112]:
channel3_segment['fig_raw']

In [113]:
channel3_segment['fig_hill']

In [114]:
channel4_segment = response_curves.responses('segment', model['full_model'], X, 'publ_pulsepoint_count', 15000, 100, 'Specialty', 'date', pulse_lags)

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

In [115]:
channel4_segment['fig_raw']

In [116]:
channel4_segment['fig_hill']

In [117]:
channel5_segment = response_curves.responses('segment', model['full_model'], X, 'deep_intent_count', 35000, 100, 'Specialty', 'date', deep_lags)

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:122: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `fr

...

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in true_divide

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

invalid value encountered in true_divide

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in power



Error - curve_fit failed


D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in true_divide

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

invalid value encountered in true_divide

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in power

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide b

Error - curve_fit failed


D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in true_divide

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

invalid value encountered in true_divide

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in power



In [118]:
channel5_segment['fig_raw']

In [119]:
channel5_segment['fig_hill']

# Reponses - simulating segments as well

In [44]:
channels = ['P1_Arikayce', 'P2_Arikayce', 'sfmc_opened_email', 'publ_pulsepoint_count', 'deep_intent_count']
specialties = [x for x in df_t.columns if x.startswith('Specialty_')]
lag_dv = [x for x in df_t.columns if 'rx_count_lag' in x]
lag_channels = [x for x in df_t.columns if ('lag' in x) & ('rx_count' not in x)]
X = df_t[channels + lag_channels + lag_dv + specialties + ['Specialty']]
X[channels + lag_channels + specialties] = 0
p1_lags = [x for x in lag_channels if 'P1' in x]
p2_lags = [x for x in lag_channels if 'P2' in x]
email_lags = [x for x in lag_channels if 'email' in x]
pulse_lags = [x for x in lag_channels if 'pulse' in x]
deep_lags = [x for x in lag_channels if 'deep' in x]

channel1_segment_v2 = response_curves.responses_segment(model['full_model'], X, 'P1_Arikayce', 1000, 5, specialties, 'Specialty', p1_lags)
channel2_segment_v2 = response_curves.responses_segment(model['full_model'], X, 'P2_Arikayce', 200, 1, specialties, 'Specialty', p2_lags)
channel3_segment_v2 = response_curves.responses_segment(model['full_model'], X, 'sfmc_opened_email', 2000, 10, specialties, 'Specialty', email_lags)
channel4_segment_v2 = response_curves.responses_segment(model['full_model'], X, 'publ_pulsepoint_count', 15000, 100, specialties, 'Specialty', pulse_lags)
channel5_segment_v2 = response_curves.responses_segment(model['full_model'], X, 'deep_intent_count', 25000, 100, specialties, 'Specialty', deep_lags)

D:\Users\hartsingh\AppData\Roaming\Python\Python37\site-packages\pandas\core\frame.py:3645: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in power

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curv

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in power



Error - curve_fit failed


D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in true_divide

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

invalid value encountered in true_divide

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in power



Error - curve_fit failed


...

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in true_divide

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

invalid value encountered in true_divide

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in power



Error - curve_fit failed


D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in true_divide

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

invalid value encountered in true_divide

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in power



Error - curve_fit failed


D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in true_divide

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

invalid value encountered in true_divide

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in power

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide by zero encountered in reciprocal

D:\Users\hartsingh\Documents\Projects\commercial-analytics\promotion_response\research\mmm_response_curves.py:21: RuntimeWarning:

divide b

In [72]:
channel1_segment_v2['fig_raw']

In [73]:
channel1_segment_v2['fig_hill']

In [74]:
channel2_segment_v2['fig_raw']

In [75]:
channel2_segment_v2['fig_hill']

In [76]:
channel3_segment_v2['fig_raw']

In [77]:
channel3_segment_v2['fig_hill']

In [78]:
channel4_segment_v2['fig_raw']

In [79]:
channel4_segment_v2['fig_hill']

In [80]:
channel5_segment_v2['fig_raw']

In [81]:
channel5_segment_v2['fig_hill']